In [ ]:
# %%
# 🔹 1. Importar bibliotecas necessárias
import os
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline

# %%
# 🔹 2. Verificar dispositivo disponível
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"✅ Dispositivo ativo: {device.upper()}")

# %%
# 🔹 3. Definir caminho do modelo local (ajuste conforme o teu projeto Django)
# Exemplo: "C:/Users/Emilio/dev/elearning/ml_models/DialoGPT-medium"
MODEL_PATH = os.path.join(os.getcwd(), "ml_models", "DialoGPT-medium")

if not os.path.exists(MODEL_PATH):
    raise FileNotFoundError(f"❌ Modelo não encontrado em {MODEL_PATH}")

print(f"📁 Modelo localizado em: {MODEL_PATH}")

# %%
# 🔹 4. Carregar tokenizer e modelo
try:
    print("🚀 Carregando modelo DialoGPT-medium localmente...")

    tokenizer = AutoTokenizer.from_pretrained(
        MODEL_PATH,
        local_files_only=True
    )

    model = AutoModelForCausalLM.from_pretrained(
        MODEL_PATH,
        dtype=torch.float32,
        local_files_only=True
    ).to(device)

    if tokenizer.pad_token is None:
        tokenizer.pad_token = tokenizer.eos_token

    print("✅ Modelo e tokenizer carregados com sucesso!")

except Exception as e:
    print(f"❌ Erro ao carregar o modelo: {str(e)}")

# %%
# 🔹 5. Criar o pipeline de geração de texto
try:
    chat_pipeline = pipeline(
        "text-generation",
        model=model,
        tokenizer=tokenizer,
        device_map="auto" if torch.cuda.is_available() else None,
        max_length=1000,
        temperature=0.8,
        top_p=0.9,
        pad_token_id=tokenizer.eos_token_id
    )
    print("✅ Pipeline inicializado com sucesso!")

except Exception as e:
    print(f"❌ Erro ao criar pipeline: {str(e)}")

# %%
# 🔹 6. Testar o modelo com um prompt simples
prompt = "Olá! Podes gerar um quiz simples sobre aprendizado de máquina?"

try:
    response = chat_pipeline(
        prompt,
        max_new_tokens=150,
        num_return_sequences=1
    )

    print("\n🧩 Resposta gerada:\n")
    print(response[0]['generated_text'])
    print("Bie!!!")

except Exception as e:
    print(f"❌ Erro ao gerar texto: {str(e)}")

# %%
# 🔹 7. (Opcional) Liberar memória GPU
if torch.cuda.is_available():
    torch.cuda.empty_cache()
    print("🧹 Cache da GPU liberado.")


✅ Dispositivo ativo: CPU
📁 Modelo localizado em: d:\Emilio\TWIGG\twigg\twigg\elearning\ml_models\DialoGPT-medium
🚀 Carregando modelo DialoGPT-medium localmente...


Device set to use cpu


✅ Modelo e tokenizer carregados com sucesso!
✅ Pipeline inicializado com sucesso!

🧩 Resposta gerada:

Olá! Podes gerar um quiz simples sobre aprendizado de máquina?
Bie!!!


In [1]:
# %%
# 🎯 SEÇÃO DE CHAT INTERATIVA - TESTE DIALOGPT

def chat_with_dialogpt():
    """
    Função interativa para testar respostas do DialoGPT
    """
    print("🤖 CHAT COM DIALOGPT-MEDIUM")
    print("=" * 50)
    print("Comandos:")
    print("  - Digite sua mensagem para conversar")
    print("  - 'quit' ou 'sair' para encerrar")
    print("  - 'clear' para limpar a conversa")
    print("  - 'test quiz' para testar geração de quiz")
    print("  - 'settings' para ajustar parâmetros")
    print("=" * 50)
    
    # Histórico da conversa
    conversation_history = []
    current_settings = {
        'max_tokens': 150,
        'temperature': 0.8,
        'top_p': 0.9
    }
    
    while True:
        try:
            # Input do usuário
            user_input = input("\n👤 Você: ").strip()
            
            # Comandos especiais
            if user_input.lower() in ['quit', 'sair', 'exit']:
                print("👋 Até logo!")
                break
                
            elif user_input.lower() == 'clear':
                conversation_history.clear()
                print("🗑️ Histórico limpo!")
                continue
                
            elif user_input.lower() == 'test quiz':
                user_input = """
                Gere um quiz com 3 questões sobre inteligência artificial em português.
                Retorne APENAS JSON no formato:
                {
                    "title": "Quiz sobre IA",
                    "questions": [
                        {
                            "question_text": "Pergunta aqui",
                            "options": [
                                {"text": "Opção A", "is_correct": false},
                                {"text": "Opção B", "is_correct": true},
                                {"text": "Opção C", "is_correct": false},
                                {"text": "Opção D", "is_correct": false}
                            ]
                        }
                    ]
                }
                """
                print("🧪 Testando geração de quiz...")
                
            elif user_input.lower() == 'settings':
                print("⚙️ Configurações atuais:")
                for key, value in current_settings.items():
                    print(f"  {key}: {value}")
                
                change = input("Alterar? (s/n): ").lower()
                if change == 's':
                    try:
                        max_tokens = input(f"Max tokens [{current_settings['max_tokens']}]: ")
                        if max_tokens:
                            current_settings['max_tokens'] = int(max_tokens)
                            
                        temperature = input(f"Temperature [{current_settings['temperature']}]: ")
                        if temperature:
                            current_settings['temperature'] = float(temperature)
                            
                        top_p = input(f"Top-p [{current_settings['top_p']}]: ")
                        if top_p:
                            current_settings['top_p'] = float(top_p)
                            
                        print("✅ Configurações atualizadas!")
                    except ValueError:
                        print("❌ Valores inválidos! Mantendo configurações anteriores.")
                continue
            
            # Construir prompt com histórico (se houver)
            if conversation_history:
                # Manter apenas últimos 4 exchanges para não exceder contexto
                recent_history = conversation_history[-4:]
                full_prompt = "\n".join([f"👤 {msg['user']}\n🤖 {msg['bot']}" for msg in recent_history])
                full_prompt += f"\n👤 {user_input}\n🤖"
            else:
                full_prompt = f"👤 {user_input}\n🤖"
            
            # Gerar resposta
            print("⏳ Gerando resposta...")
            
            response = chat_pipeline(
                full_prompt,
                max_new_tokens=current_settings['max_tokens'],
                temperature=current_settings['temperature'],
                top_p=current_settings['top_p'],
                do_sample=True,
                num_return_sequences=1,
                pad_token_id=tokenizer.eos_token_id,
                return_full_text=False
            )
            
            # Extrair resposta gerada
            generated_text = response[0]['generated_text'].strip()
            
            # Limpar resposta (remover possíveis repetições do prompt)
            if "🤖" in generated_text:
                generated_text = generated_text.split("🤖")[-1].strip()
            
            # Adicionar ao histórico
            conversation_history.append({
                'user': user_input,
                'bot': generated_text
            })
            
            # Mostrar resposta
            print(f"\n🤖 DialoGPT: {generated_text}")
            
            # Estatísticas
            input_tokens = len(tokenizer.encode(full_prompt))
            output_tokens = len(tokenizer.encode(generated_text))
            print(f"📊 Tokens: {input_tokens} (input) + {output_tokens} (output) = {input_tokens + output_tokens} (total)")
            
        except KeyboardInterrupt:
            print("\n\n🛑 Chat interrompido pelo usuário")
            break
        except Exception as e:
            print(f"❌ Erro: {str(e)}")
            continue
    
    # Limpar memória ao final
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
        print("🧹 Cache da GPU liberado.")

# %%
# 🚀 INICIAR CHAT
chat_with_dialogpt()

🤖 CHAT COM DIALOGPT-MEDIUM
Comandos:
  - Digite sua mensagem para conversar
  - 'quit' ou 'sair' para encerrar
  - 'clear' para limpar a conversa
  - 'test quiz' para testar geração de quiz
  - 'settings' para ajustar parâmetros



👤 Você:  test quiz


🧪 Testando geração de quiz...
⏳ Gerando resposta...
❌ Erro: name 'chat_pipeline' is not defined



👤 Você:  quit


👋 Até logo!


NameError: name 'torch' is not defined

In [ ]:
# %%
# 🧪 TESTES ESPECÍFICOS PARA GERAÇÃO DE QUIZ

def test_quiz_generation():
    """
    Testa especificamente a geração de quizzes
    """
    print("🧪 TESTE DE GERAÇÃO DE QUIZ")
    print("=" * 50)
    
    test_prompts = [
        {
            "name": "Quiz básico PT",
            "prompt": """
            Gere um quiz com 2 questões sobre machine learning em português.
            Formato JSON:
            {
                "title": "Quiz ML",
                "questions": [
                    {
                        "question_text": "Pergunta",
                        "options": [
                            {"text": "A", "is_correct": false},
                            {"text": "B", "is_correct": true},
                            {"text": "C", "is_correct": false},
                            {"text": "D", "is_correct": false}
                        ]
                    }
                ]
            }
            """
        },
        {
            "name": "Quiz inglês",
            "prompt": """
            Create a 2-question quiz about Python programming in English.
            JSON format only:
            {
                "title": "Python Quiz",
                "questions": [
                    {
                        "question_text": "Question",
                        "options": [
                            {"text": "A", "is_correct": false},
                            {"text": "B", "is_correct": true},
                            {"text": "C", "is_correct": false},
                            {"text": "D", "is_correct": false}
                        ]
                    }
                ]
            }
            """
        }
    ]
    
    for test in test_prompts:
        print(f"\n🎯 Teste: {test['name']}")
        print("─" * 30)
        
        try:
            response = chat_pipeline(
                test['prompt'],
                max_new_tokens=300,
                temperature=0.7,
                top_p=0.9,
                do_sample=True,
                num_return_sequences=1
            )
            
            generated_text = response[0]['generated_text'].strip()
            print("📝 Resposta:")
            print(generated_text)
            
            # Tentar extrair JSON
            import re
            json_match = re.search(r'\{.*\}', generated_text, re.DOTALL)
            if json_match:
                print("\n✅ JSON detectado!")
                try:
                    import json
                    quiz_data = json.loads(json_match.group())
                    print("📊 Estrutura válida!")
                except json.JSONDecodeError:
                    print("❌ JSON inválido")
            else:
                print("❌ Nenhum JSON encontrado")
                
        except Exception as e:
            print(f"❌ Erro: {str(e)}")
        
        print("─" * 30)

# %%
# 🧪 EXECUTAR TESTES DE QUIZ
test_quiz_generation()

In [ ]:
# %%
# 📊 ANALISADOR DE RESPOSTAS

def analyze_response(prompt, max_tokens=150, temperature=0.8):
    """
    Analisa detalhadamente uma resposta do DialoGPT
    """
    print(f"🔍 ANALISANDO: '{prompt[:50]}...'")
    print("─" * 50)
    
    try:
        # Gerar resposta
        response = chat_pipeline(
            prompt,
            max_new_tokens=max_tokens,
            temperature=temperature,
            top_p=0.9,
            do_sample=True,
            num_return_sequences=1,
            return_full_text=True
        )
        
        full_text = response[0]['generated_text']
        
        # Análise
        input_tokens = len(tokenizer.encode(prompt))
        output_tokens = len(tokenizer.encode(full_text)) - input_tokens
        total_tokens = input_tokens + output_tokens
        
        print(f"📝 Resposta completa:\n{full_text}")
        print("─" * 50)
        print(f"📊 Estatísticas:")
        print(f"   • Tokens entrada: {input_tokens}")
        print(f"   • Tokens saída: {output_tokens}") 
        print(f"   • Tokens total: {total_tokens}")
        print(f"   • Temperatura: {temperature}")
        
        # Verificar se contém JSON
        import re
        if re.search(r'\{.*\}', full_text, re.DOTALL):
            print("✅ CONTÉM JSON")
        else:
            print("❌ SEM JSON")
            
        return full_text
        
    except Exception as e:
        print(f"❌ Erro: {str(e)}")
        return None

# %%
# 🧪 TESTAR ANÁLISE COM DIFERENTES PROMPTS
test_prompts = [
    "Gere um quiz sobre Django em português com JSON",
    "Create a Python quiz in English with JSON format",
    "Como funciona o machine learning?",
    "Explique transformers em NLP"
]

for prompt in test_prompts:
    analyze_response(prompt)
    print("\n" + "="*50 + "\n")

In [ ]:
# %%
# 🎛️ CONFIGURADOR DE PARÂMETROS

def parameter_sweep():
    """
    Testa diferentes combinações de parâmetros
    """
    print("🎛️ TESTE DE PARÂMETROS")
    print("=" * 50)
    
    base_prompt = "Gere 2 questões sobre Python em JSON"
    
    temperatures = [0.5, 0.7, 0.9, 1.1]
    max_tokens_list = [100, 200, 300]
    
    for temp in temperatures:
        for max_tok in max_tokens_list:
            print(f"\n🔧 Temp: {temp}, MaxTokens: {max_tok}")
            print("─" * 30)
            
            try:
                response = chat_pipeline(
                    base_prompt,
                    max_new_tokens=max_tok,
                    temperature=temp,
                    top_p=0.9,
                    do_sample=True,
                    num_return_sequences=1
                )
                
                text = response[0]['generated_text']
                print(f"📝: {text[:100]}...")
                
            except Exception as e:
                print(f"❌ Erro: {str(e)}")

# %%
# 🎛️ EXECUTAR VARREdura DE PARÂMETROS (OPCIONAL)
# parameter_sweep()

In [ ]:
# %%
# 💾 SALVAR RESULTADOS DOS TESTES

def save_test_results():
    """
    Salva os resultados dos testes em arquivo
    """
    import datetime
    import json
    
    timestamp = datetime.datetime.now().strftime("%Y%m%d_%H%M%S")
    filename = f"dialogpt_test_{timestamp}.txt"
    
    test_prompt = "Gere um quiz sobre Django com JSON"
    
    try:
        response = chat_pipeline(
            test_prompt,
            max_new_tokens=200,
            temperature=0.8,
            num_return_sequences=1
        )
        
        result = {
            'timestamp': timestamp,
            'prompt': test_prompt,
            'response': response[0]['generated_text'],
            'model': 'DialoGPT-medium',
            'parameters': {
                'max_tokens': 200,
                'temperature': 0.8,
                'top_p': 0.9
            }
        }
        
        with open(filename, 'w', encoding='utf-8') as f:
            json.dump(result, f, indent=2, ensure_ascii=False)
            
        print(f"✅ Resultados salvos em: {filename}")
        
    except Exception as e:
        print(f"❌ Erro ao salvar: {str(e)}")

# %%
# 💾 SALVAR TESTE (OPCIONAL)
# save_test_results()

In [2]:
# %%
# 🎯 SEÇÃO DE CHAT INTERATIVA COMPLETA - DIALOGPT MEDIUM

import os
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline
import json
import re

# %%
# 🔧 CONFIGURAÇÃO INICIAL
def setup_dialogpt():
    """Configura e retorna o pipeline do DialoGPT"""
    print("🚀 Inicializando DialoGPT-medium...")
    
    # Definir dispositivo
    device = "cuda" if torch.cuda.is_available() else "cpu"
    print(f"✅ Dispositivo: {device.upper()}")
    
    # Caminho do modelo (ajuste conforme sua estrutura)
    MODEL_PATH = os.path.join(os.getcwd(), "ml_models", "DialoGPT-medium")
    
    if not os.path.exists(MODEL_PATH):
        print(f"❌ Modelo não encontrado em: {MODEL_PATH}")
        print("📁 Verifique se a pasta contém:")
        print("   - config.json")
        print("   - pytorch_model.bin") 
        print("   - tokenizer_config.json")
        print("   - vocab.json")
        print("   - merges.txt")
        return None
    
    try:
        # Carregar tokenizer
        tokenizer = AutoTokenizer.from_pretrained(
            MODEL_PATH,
            local_files_only=True
        )
        
        if tokenizer.pad_token is None:
            tokenizer.pad_token = tokenizer.eos_token
        
        # Carregar modelo
        model = AutoModelForCausalLM.from_pretrained(
            MODEL_PATH,
            dtype=torch.float32,
            device_map="auto" if torch.cuda.is_available() else None,
            local_files_only=True
        )
        
        # Criar pipeline
        chat_pipeline = pipeline(
            "text-generation",
            model=model,
            tokenizer=tokenizer,
            dtype=torch.float32,
            device_map="auto" if torch.cuda.is_available() else None,
            max_length=1024,
            pad_token_id=tokenizer.eos_token_id
        )
        
        print("✅ DialoGPT-medium carregado com sucesso!")
        return chat_pipeline, tokenizer
        
    except Exception as e:
        print(f"❌ Erro ao carregar modelo: {str(e)}")
        return None, None

# %%
# 🚀 INICIALIZAR O MODELO
chat_pipeline, tokenizer = setup_dialogpt()

if chat_pipeline is None:
    print("❌ Não foi possível inicializar o modelo. Verifique o caminho e os arquivos.")
else:
    print("🎉 Modelo pronto para uso!")

# %%
# 💬 FUNÇÃO DE CHAT INTERATIVO
def chat_with_dialogpt():
    """
    Chat interativo com DialoGPT-medium
    """
    if chat_pipeline is None:
        print("❌ Modelo não inicializado. Execute a célula de configuração primeiro.")
        return
    
    print("\n" + "🤖 CHAT COM DIALOGPT-MEDIUM" + "="*50)
    print("Comandos:")
    print("  - Digite sua mensagem para conversar")
    print("  - 'quit' ou 'sair' para encerrar")
    print("  - 'clear' para limpar o histórico")
    print("  - 'test quiz' para testar geração de quiz")
    print("  - 'settings' para ajustar parâmetros")
    print("="*50)
    
    conversation_history = []
    current_settings = {
        'max_tokens': 150,
        'temperature': 0.8,
        'top_p': 0.9
    }
    
    while True:
        try:
            user_input = input("\n👤 Você: ").strip()
            
            if user_input.lower() in ['quit', 'sair', 'exit']:
                print("👋 Até logo!")
                break
                
            elif user_input.lower() == 'clear':
                conversation_history.clear()
                print("🗑️ Histórico limpo!")
                continue
                
            elif user_input.lower() == 'test quiz':
                user_input = """
                Gere um quiz com 2 questões sobre programação Python em português.
                Retorne APENAS JSON no formato:
                {
                    "title": "Quiz Python",
                    "questions": [
                        {
                            "question_text": "Pergunta aqui",
                            "type": "multiple_choice",
                            "options": [
                                {"text": "Opção A", "is_correct": false},
                                {"text": "Opção B", "is_correct": true},
                                {"text": "Opção C", "is_correct": false},
                                {"text": "Opção D", "is_correct": false}
                            ]
                        }
                    ]
                }
                """
                print("🧪 Testando geração de quiz...")
                
            elif user_input.lower() == 'settings':
                print("⚙️ Configurações atuais:")
                for key, value in current_settings.items():
                    print(f"  {key}: {value}")
                
                change = input("Alterar? (s/n): ").lower()
                if change == 's':
                    try:
                        max_tokens = input(f"Max tokens [{current_settings['max_tokens']}]: ")
                        if max_tokens:
                            current_settings['max_tokens'] = int(max_tokens)
                            
                        temperature = input(f"Temperature [{current_settings['temperature']}]: ")
                        if temperature:
                            current_settings['temperature'] = float(temperature)
                            
                        top_p = input(f"Top-p [{current_settings['top_p']}]: ")
                        if top_p:
                            current_settings['top_p'] = float(top_p)
                            
                        print("✅ Configurações atualizadas!")
                    except ValueError:
                        print("❌ Valores inválidos! Mantendo configurações anteriores.")
                continue
            
            # Construir prompt
            if conversation_history:
                recent_history = conversation_history[-3:]  # Manter último contexto
                context = "\n".join([f"User: {msg['user']}\nBot: {msg['bot']}" for msg in recent_history])
                full_prompt = f"{context}\nUser: {user_input}\nBot:"
            else:
                full_prompt = f"User: {user_input}\nBot:"
            
            print("⏳ Gerando resposta...")
            
            # Gerar resposta
            response = chat_pipeline(
                full_prompt,
                max_new_tokens=current_settings['max_tokens'],
                temperature=current_settings['temperature'],
                top_p=current_settings['top_p'],
                do_sample=True,
                num_return_sequences=1,
                pad_token_id=tokenizer.eos_token_id,
                return_full_text=False
            )
            
            generated_text = response[0]['generated_text'].strip()
            
            # Limpar resposta
            if "Bot:" in generated_text:
                generated_text = generated_text.split("Bot:")[-1].strip()
            
            # Adicionar ao histórico
            conversation_history.append({
                'user': user_input,
                'bot': generated_text
            })
            
            # Mostrar resposta
            print(f"\n🤖 DialoGPT: {generated_text}")
            
            # Estatísticas
            input_tokens = len(tokenizer.encode(full_prompt))
            output_tokens = len(tokenizer.encode(generated_text))
            print(f"📊 Tokens: {input_tokens} (input) + {output_tokens} (output)")
            
            # Verificar JSON
            if re.search(r'\{.*\}', generated_text, re.DOTALL):
                print("✅ JSON detectado na resposta!")
                
        except KeyboardInterrupt:
            print("\n\n🛑 Chat interrompido")
            break
        except Exception as e:
            print(f"❌ Erro: {str(e)}")
    
    # Limpar memória
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
        print("🧹 Cache limpo")

# %%
# 🚀 INICIAR CHAT (Execute esta célula para começar)
if chat_pipeline is not None:
    chat_with_dialogpt()
else:
    print("❌ Execute primeiro a célula de configuração do modelo")

🚀 Inicializando DialoGPT-medium...
✅ Dispositivo: CPU


Device set to use cpu


✅ DialoGPT-medium carregado com sucesso!
🎉 Modelo pronto para uso!

🤖 CHAT COM DIALOGPT-MEDIUM==================================================
Comandos:
  - Digite sua mensagem para conversar
  - 'quit' ou 'sair' para encerrar
  - 'clear' para limpar o histórico
  - 'test quiz' para testar geração de quiz
  - 'settings' para ajustar parâmetros



👤 Você:  test quiz


🧪 Testando geração de quiz...
⏳ Gerando resposta...

🤖 DialoGPT: 
📊 Tokens: 575 (input) + 0 (output)


🛑 Chat interrompido


In [3]:
# %%
# 🔧 VERSÃO CORRIGIDA - CHAT COM PROMPTS OTIMIZADOS

def chat_with_dialogpt_fixed():
    """
    Chat corrigido com prompts otimizados para DialoGPT
    """
    if chat_pipeline is None:
        print("❌ Modelo não inicializado.")
        return
    
    print("\n" + "🤖 CHAT CORRIGIDO - DIALOGPT MEDIUM" + "="*50)
    print("Comandos:")
    print("  - Digite normalmente para conversar")
    print("  - 'quiz' - Gerar quiz simples")
    print("  - 'json' - Testar geração JSON")
    print("  - 'clear' - Limpar histórico")
    print("  - 'quit' - Sair")
    print("="*50)
    
    conversation_history = []
    current_settings = {
        'max_tokens': 200,
        'temperature': 0.9,  # Aumentar temperatura para mais criatividade
        'top_p': 0.95
    }
    
    while True:
        try:
            user_input = input("\n👤 Você: ").strip()
            
            if user_input.lower() in ['quit', 'sair', 'exit']:
                print("👋 Até logo!")
                break
                
            elif user_input.lower() == 'clear':
                conversation_history.clear()
                print("🗑️ Histórico limpo!")
                continue
                
            elif user_input.lower() == 'quiz':
                # ✅ PROMPT MAIS SIMPLES E DIRETO
                user_input = "Crie 2 perguntas de múltipla escolha sobre Python. Formato: pergunta? a) opção b) opção c) opção d) opção. Resposta: letra."
                print("🧪 Gerando quiz simples...")
                
            elif user_input.lower() == 'json':
                # ✅ PROMPT JSON SIMPLIFICADO
                user_input = "Retorne JSON: {'quiz': [{'pergunta': 'exemplo', 'opcoes': ['A','B','C','D'], 'correta': 'A'}]}"
                print("🧪 Testando JSON...")
            
            # ✅ PROMPT MAIS CURTO E DIRETO
            if conversation_history:
                # Manter apenas última troca para contexto
                last_exchange = conversation_history[-1]
                context = f"Usuário: {last_exchange['user']}\nAssistant: {last_exchange['bot']}\nUsuário: {user_input}\nAssistant:"
            else:
                context = f"Usuário: {user_input}\nAssistant:"
            
            print("⏳ Gerando...")
            
            # ✅ CONFIGURAÇÕES OTIMIZADAS
            response = chat_pipeline(
                context,
                max_new_tokens=current_settings['max_tokens'],
                temperature=current_settings['temperature'],
                top_p=current_settings['top_p'],
                do_sample=True,
                num_return_sequences=1,
                pad_token_id=tokenizer.eos_token_id,
                return_full_text=False,
                repetition_penalty=1.1  # Evitar repetições
            )
            
            if response and len(response) > 0:
                generated_text = response[0]['generated_text'].strip()
                
                # Limpar resposta
                if "Assistant:" in generated_text:
                    generated_text = generated_text.split("Assistant:")[-1].strip()
                
                # Se ainda vazia, tentar fallback
                if not generated_text or len(generated_text) < 5:
                    generated_text = "(Sem resposta gerada. Tente um prompt mais simples.)"
                
            else:
                generated_text = "(Erro na geração)"
            
            # Adicionar ao histórico
            conversation_history.append({
                'user': user_input,
                'bot': generated_text
            })
            
            # Mostrar resposta
            print(f"\n🤖 DialoGPT: {generated_text}")
            
            # Estatísticas
            input_tokens = len(tokenizer.encode(context))
            output_tokens = len(tokenizer.encode(generated_text))
            print(f"📊 Tokens: {input_tokens} (entrada) + {output_tokens} (saída)")
            
        except KeyboardInterrupt:
            print("\n\n🛑 Chat interrompido")
            break
        except Exception as e:
            print(f"❌ Erro: {str(e)}")
            # Fallback para continuar
            conversation_history.append({
                'user': user_input,
                'bot': f"(Erro: {str(e)})"
            })

# %%
# 🚀 EXECUTAR CHAT CORRIGIDO
if chat_pipeline is not None:
    chat_with_dialogpt_fixed()
else:
    print("❌ Modelo não inicializado")


🤖 CHAT CORRIGIDO - DIALOGPT MEDIUM==================================================
Comandos:
  - Digite normalmente para conversar
  - 'quiz' - Gerar quiz simples
  - 'json' - Testar geração JSON
  - 'clear' - Limpar histórico
  - 'quit' - Sair



👤 Você:  quiz


🧪 Gerando quiz simples...
⏳ Gerando...

🤖 DialoGPT: letra e ou.
📊 Tokens: 63 (entrada) + 6 (saída)



👤 Você:  json


🧪 Testando JSON...
⏳ Gerando...

🤖 DialoGPT: retorned
📊 Tokens: 124 (entrada) + 2 (saída)



👤 Você:  quit


👋 Até logo!


In [5]:
# %%
# 🧪 TESTES DE PROMPT EFICAZES

def test_effective_prompts():
    """Testa diferentes tipos de prompt para ver o que funciona"""
    if chat_pipeline is None:
        return
    
    test_prompts = [
        # ✅ PROMPTS QUE DEVEM FUNCIONAR
        {
            "name": "Conversa simples",
            "prompt": "Olá! Como você está hoje?",
            "desc": "Prompt básico de conversa"
        },
        {
            "name": "Pergunta direta", 
            "prompt": "O que é Python?",
            "desc": "Pergunta factual simples"
        },
        {
            "name": "Quiz simples",
            "prompt": "Faça uma pergunta sobre programação com 4 opções de resposta.",
            "desc": "Instrução simples de quiz"
        },
        {
            "name": "Comando JSON",
            "prompt": "Retorne um exemplo de JSON com uma pergunta de quiz.",
            "desc": "Solicitação JSON direta"
        }
    ]
    
    print("🧪 TESTANDO PROMPTS EFICAZES")
    print("=" * 50)
    
    for test in test_prompts:
        print(f"\n🎯 {test['name']}: {test['desc']}")
        print(f"📝 Prompt: {test['prompt']}")
        print("─" * 40)
        
        try:
            response = chat_pipeline(
                test['prompt'],
                max_new_tokens=100,
                temperature=0.9,
                do_sample=True,
                num_return_sequences=1
            )
            
            if response and len(response) > 0:
                result = response[0]['generated_text'].strip()
                print(f"🤖 Resposta: {result}")
                print(response)
                
                # Análise
                input_len = len(tokenizer.encode(test['prompt']))
                output_len = len(tokenizer.encode(result))
                print(f"📊 Tokens: {input_len} → {output_len}")
                
            else:
                print("❌ Nenhuma resposta gerada")
                
        except Exception as e:
            print(f"❌ Erro: {str(e)}")

# %%
# 🧪 EXECUTAR TESTES DE PROMPT
if chat_pipeline is not None:
    test_effective_prompts()

🧪 TESTANDO PROMPTS EFICAZES

🎯 Conversa simples: Prompt básico de conversa
📝 Prompt: Olá! Como você está hoje?
────────────────────────────────────────
🤖 Resposta: Olá! Como você está hoje?
[{'generated_text': 'Olá! Como você está hoje?'}]
📊 Tokens: 12 → 12

🎯 Pergunta direta: Pergunta factual simples
📝 Prompt: O que é Python?
────────────────────────────────────────
🤖 Resposta: O que é Python? Se que querem a ideologia. Quais aparentement, mas meu correr, quando tava a mais.
[{'generated_text': 'O que é Python? Se que querem a ideologia. Quais aparentement, mas meu correr, quando tava a mais.'}]
📊 Tokens: 5 → 35

🎯 Quiz simples: Instrução simples de quiz
📝 Prompt: Faça uma pergunta sobre programação com 4 opções de resposta.
────────────────────────────────────────
🤖 Resposta: Faça uma pergunta sobre programação com 4 opções de resposta.p
[{'generated_text': 'Faça uma pergunta sobre programação com 4 opções de resposta.p'}]
📊 Tokens: 24 → 25

🎯 Comando JSON: Solicitação JSON direta
📝 